# Open Data

In [1]:
import pandas as pd
df = pd.read_csv('dataset_tweet_sentimen_tayangan_tv.csv')
df

Id Sentiment           Acara TV  Jumlah Retweet  \
0      1  positive  HitamPutihTransTV              12   
1      2  positive  HitamPutihTransTV               6   
2      3  positive  HitamPutihTransTV               9   
3      4  positive  HitamPutihTransTV               2   
4      5  positive  HitamPutihTransTV               1   
..   ...       ...                ...             ...   
395  396  negative   MataNajwaMetroTV               0   
396  397  negative   MataNajwaMetroTV               0   
397  398  negative   MataNajwaMetroTV               0   
398  399  negative   MataNajwaMetroTV               0   
399  400  negative   MataNajwaMetroTV               0   

                                            Text Tweet  
0    Undang @N_ShaniJKT48 ke hitamputih, pemenang S...  
1    Selamat berbuka puasa Semoga amal ibadah hari ...  
2    Ada nih di trans7 hitam putih, dia dpt penghar...  
3          selamat ya mas @adietaufan masuk hitamputih  
4                    Asiknya nonton Hitam Putih Trans7  
..                                                 ...  
395  ini apa banget deh gw paling kesel klo orang2 ...  
396  Orang miskin semakin miskin klo sekolah melaku...  
397  ga boLeh emosi, cepat tua, nonton #matanajwame...  
398  dr penampilan saja kyk preman taunya bkin kisr...  
399  Jawab aja ga usah berbelit-belit. Muter2 ga je...  

[400 rows x 5 columns]

In [3]:
with open('dataset_tweet_sentimen_tayangan_tv.csv', 'r', encoding="utf8") as nodecsv: 
    # Buka file 
    csvreader = csv.reader(nodecsv) # membaca data 
    # Menyusun data dalam list dan menghilangkan header data 
    csv = [n for n in csvreader][1:]

In [4]:
csv

[['1',
  'positive',
  'HitamPutihTransTV',
  '12',
  'Undang @N_ShaniJKT48 ke hitamputih, pemenang SSK JKT48 harusnya mJKT48 ini lebih Layak di Undang karena prestasinya'],
 ['2',
  'positive',
  'HitamPutihTransTV',
  '6',
  'Selamat berbuka puasa Semoga amal ibadah hari ni diterima Allah #hitamputih'],
 ['3',
  'positive',
  'HitamPutihTransTV',
  '9',
  'Ada nih di trans7 hitam putih, dia dpt penghargaan juga di norwegia #hitamputih'],
 ['4',
  'positive',
  'HitamPutihTransTV',
  '2',
  'selamat ya mas @adietaufan masuk hitamputih'],
 ['5',
  'positive',
  'HitamPutihTransTV',
  '1',
  'Asiknya nonton Hitam Putih Trans7'],
 ['6',
  'positive',
  'HitamPutihTransTV',
  '2',
  '@TRANS7 acara paling komplit dan menarik apalagi ada hitam putih'],
 ['7',
  'positive',
  'HitamPutihTransTV',
  '1',
  'hitam putih T7 inspiratif banget'],
 ['8',
  'positive',
  'HitamPutihTransTV',
  '3',
  'Suka banget dengan acara hitam putih'],
 ['9', 'positive', 'HitamPutihTransTV', '0', 'Keren lu bro

# A. Naive Bayes

In [2]:
import nltk 
import random 
from sklearn.model_selection import train_test_split 
from nltk.classify.scikitlearn import SklearnClassifier 
import pickle 
from sklearn.naive_bayes import MultinomialNB, BernoulliNB 
from sklearn.linear_model import LogisticRegression, SGDClassifier 
from sklearn.svm import SVC, LinearSVC, NuSVC 
from nltk.classify import ClassifierI 
from statistics import mode 
from nltk.tokenize import word_tokenize 
import re 
import csv 
from nltk.corpus import stopwords 
import string 
import emoji

In [5]:
emoticons_str = r""" 
    (?: 
        [:=;] # Eyes 
        [oO\-]? # Nose (optional) 
        [D\)\]\(\]/\\OpP] # Mouth 
    )""" 

regex_str = [] 
regex_str.append(emoticons_str) 
regex_str.append(r'<[^>]+>')# HTML tags 
regex_str.append(r'(?:@[\w_]+)')# @-mentions 
regex_str.append(r'(?:&[\w_]+)') 
regex_str.append(r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)") # hash-tags 
regex_str.append(r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+') # URLs 
regex_str.append(r'(?:(?:\d+,?)+(?:\.?\d+)?)') # numbers 
regex_str.append(r"(?:[a-z][a-z'\-_]+[a-z])") # words with - and ' 
regex_str.append(r'(?:[\w_]+)') # other words 
regex_str.append(r'(?:\S)') # anything else 

tokens_re = re.compile(r'('+'|'.join(regex_str)+')', re.VERBOSE | re.IGNORECASE) 
emoticon_re = re.compile(r'^'+emoticons_str+'$', re.VERBOSE | re.IGNORECASE)

In [6]:
nltk.download('punkt') 
from nlp_id.stopword import StopWord 
stopword = StopWord()

punctuation = list(string.punctuation)
stop = stopword.get_stopword() + punctuation + ['rt', 'via', '…','•','“']

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [7]:
def tokenize(s): 
    tokens = tokens_re.findall(s) 
    return tokens 

def cleanTweet(token,regex): 
    terms_all = [emoji.demojize(term) for term in token if term.lower() not in stop and not regex.match(term)] 
    return terms_all

In [8]:
tokens = [] 
for c in csv: 
    tokens.append(tokenize(c[4])) 

print(tokens[:5])

[['Undang', '@N_ShaniJKT48', 'ke', 'hitamputih', ',', 'pemenang', 'SSK', 'JKT', '48', 'harusnya', 'mJKT', '48', 'ini', 'lebih', 'Layak', 'di', 'Undang', 'karena', 'prestasinya'], ['Selamat', 'berbuka', 'puasa', 'Semoga', 'amal', 'ibadah', 'hari', 'ni', 'diterima', 'Allah', '#hitamputih'], ['Ada', 'nih', 'di', 'trans', '7', 'hitam', 'putih', ',', 'dia', 'dpt', 'penghargaan', 'juga', 'di', 'norwegia', '#hitamputih'], ['selamat', 'ya', 'mas', '@adietaufan', 'masuk', 'hitamputih'], ['Asiknya', 'nonton', 'Hitam', 'Putih', 'Trans', '7']]


In [9]:
import operator 
exclude_str = [] 
exclude_str.append(emoticons_str) 
exclude_str.append(r'<[^>]+>')# HTML tags 
exclude_str.append(r'(?:@[\w_]+)')# @-mentions 
exclude_str.append(r'(?:&[\w_]+)') 
exclude_str.append(r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)") # hash-tags 
exclude_str.append(r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+') # URLs 
exclude_str.append(r'(?:(?:\d+,?)+(?:\.?\d+)?)') # numbers
exclude_re = re.compile(r'('+'|'.join(exclude_str)+')', re.VERBOSE | re.IGNORECASE)

In [10]:
all_word=[] 
from collections import Counter 
count_all = Counter() 

for token in tokens: 
    cleanToken = cleanTweet(token,exclude_re) 
    terms_all = [term.lower() for term in cleanToken] 
    count_all.update(terms_all) 
    for w in terms_all: 
        all_word.append(w) 
print(count_all.most_common(100))

[('mata', 61), ('najwa', 60), ('hitam', 40), ('putih', 39), ('acara', 32), ('nonton', 29), ('keren', 29), ('orang', 29), ('ga', 28), ('tv', 25), ('indonesia', 21), ('ahok', 19), ('trans', 18), ('metro', 18), ('malam', 15), ('tdk', 15), ('anak', 14), ('ilc', 14), ('semoga', 13), ('menginspirasi', 13), ('andy', 13), ('seru', 11), ('suka', 10), ('liat', 10), ('miris', 10), ('tp', 10), ('gak', 10), ('tvone', 10), ('salut', 10), ('kick', 10), ('nih', 9), ('kalo', 9), ('org', 9), ('bikin', 8), ('hukum', 8), ('dg', 8), ('bapak', 8), ('debat', 8), ('anis', 8), ('undang', 7), ('hati', 7), ('kasih', 7), ('lihat', 7), ('pake', 7), ('hidup', 7), ('tak', 7), ('ngomong', 7), ('lawyers', 7), ('club', 7), ('selamat', 6), ('terima', 6), ('utk', 6), ('setuju', 6), ('lg', 6), ('dgn', 6), ('sbg', 6), ('klo', 6), ('memalukan', 6), ('mati', 6), ('bs', 6), ('kalah', 6), ('krn', 6), ('sakit', 6), ('anies', 6), ('hitamputih', 5), ('masuk', 5), ('menarik', 5), ('inspiratif', 5), ('cinta', 5), ('tamu', 5), ('kay

In [11]:
#inisialisasi lematizer dan postagger 
from nlp_id.lemmatizer import Lemmatizer 
lemmatizer = Lemmatizer()

from nlp_id.postag import PosTag 
postagger = PosTag()

In [12]:
all_stmword = [lemmatizer.lemmatize(w) for w in all_word] 
print(all_stmword[:20]) 

['undang', 'hitamputih', 'menang', 'ssk', 'jkt', 'mjkt', 'layak', 'undang', 'prestasi', 'selamat', 'buka', 'puasa', 'moga', 'amal', 'ibadah', 'ni', 'terima', 'allah', 'nih', 'trans']


In [13]:
pos = [postagger.get_pos_tag(w)[0] for w in all_stmword] 
print(pos[:10])

[('undang', 'NN'), ('hitamputih', 'VB'), ('menang', 'VB'), ('ssk', 'NN'), ('jkt', 'NN'), ('mjkt', 'NN'), ('layak', 'JJ'), ('undang', 'NN'), ('prestasi', 'NN'), ('selamat', 'JJ')]


In [14]:
allowed_word_types = ["ADV","JJ","ADJP","VB"] 
allowed_words=[w[0] for w in pos if w[1] in allowed_word_types]

In [15]:
#Menyusun distribusi kata berdasarkan kemunculannya 
allwords = nltk.FreqDist(allowed_words) 

#Mengambil 5000 pertama dari distribusi kata berdasarkan frekwensi kemunculannya 
tuple_features = list(allwords.most_common())[:5000] 
word_features = [k for (k,v) in tuple_features] 

#Memeriksa word_features 
print(word_features[:100])

['hitam', 'putih', 'nonton', 'seru', 'hidup', 'tp', 'terima', 'bikin', 'rusak', 'kalah', 'lihat', 'tunggu', 'ngomong', 'bilang', 'coba', 'selamat', 'mati', 'pimpin', 'pilih', 'bicara', 'jaga', 'hitamputih', 'masuk', 'bagus', 'tayang', 'hebat', 'dengar', 'salah', 'langsung', 'mantap', 'bangga', 'dukung', 'pikir', 'tua', 'metrotv', 'lawan', 'buka', 'ni', 'pribadi', 'beda', 'kaya', 'mimpi', 'muncul', 'butuh', 'tindak', 'cerdas', 'lucu', 'besar', 'pulang', 'bawa', 'ubah', 'miskin', 'menang', 'bantu', 'baik', 'bahas', 'jujur', 'ikut', 'takut', 'sesuai', 'lupa', 'bayar', 'kagum', 'sejuk', 'milik', 'kuat', 'jadi', 'berani', 'dki', 'uji', 'malas', 'didik', 'tai', 'lancar', 'nyanyi', 'hibur', 'ustadz', 'asli', 'ucap', 'berat', 'aneh', 'sedih', 'sulit', 'parah', 'muda', 'hendak', 'paksa', 'trus', 'ketawa', 'pergi', 'mbak', 'toleransi', 'buruk', 'medsos', 'dijalanin', 'dipikirin', 'taksi', 'pasrah', 'darurat', 'kucing']


### Menyusun training dan testing

In [16]:
document=[] 
for w in csv: 
    document.append((w[4],w[1]))

In [17]:
document

[('Undang @N_ShaniJKT48 ke hitamputih, pemenang SSK JKT48 harusnya mJKT48 ini lebih Layak di Undang karena prestasinya',
  'positive'),
 ('Selamat berbuka puasa Semoga amal ibadah hari ni diterima Allah #hitamputih',
  'positive'),
 ('Ada nih di trans7 hitam putih, dia dpt penghargaan juga di norwegia #hitamputih',
  'positive'),
 ('selamat ya mas @adietaufan masuk hitamputih', 'positive'),
 ('Asiknya nonton Hitam Putih Trans7', 'positive'),
 ('@TRANS7 acara paling komplit dan menarik apalagi ada hitam putih',
  'positive'),
 ('hitam putih T7 inspiratif banget', 'positive'),
 ('Suka banget dengan acara hitam putih', 'positive'),
 ('Keren lu bro #HitamPutihTrans7', 'positive'),
 ('Tadi ada yg liat hitam putih di trans7 ga, Ada sanggu ganteng', 'positive'),
 ('cinta mengikat silaturahmi di hati ... #LunaMaya #hitamputihtrans7 .... https://www.instagram.com/p/BTqszJ3jO9A/',
  'positive'),
 ('Terima kasih pak.... Sudah mau membantu kami untuk menyekolahkan adik saya.... #hitamputihtrans7',

In [18]:
def find_features(document): 
    words = word_tokenize(document) 
    features = {} 
    for w in word_features: 
        features[w] = (w in words) 
    return features

In [19]:
nltk.download('punkt') 
featuresets = [(find_features(rev), category) for (rev, category) in document]

print(featuresets[:5])

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[({'hitam': False, 'putih': False, 'nonton': False, 'seru': False, 'hidup': False, 'tp': False, 'terima': False, 'bikin': False, 'rusak': False, 'kalah': False, 'lihat': False, 'tunggu': False, 'ngomong': False, 'bilang': False, 'coba': False, 'selamat': False, 'mati': False, 'pimpin': False, 'pilih': False, 'bicara': False, 'jaga': False, 'hitamputih': True, 'masuk': False, 'bagus': False, 'tayang': False, 'hebat': False, 'dengar': False, 'salah': False, 'langsung': False, 'mantap': False, 'bangga': False, 'dukung': False, 'pikir': False, 'tua': False, 'metrotv': False, 'lawan': False, 'buka': False, 'ni': False, 'pribadi': False, 'beda': False, 'kaya': False, 'mimpi': False, 'muncul': False, 'butuh': False, 'tindak': False, 'cerdas': False, 'lucu': False, 'besar': False, 'pulang': False, 'bawa': False, 'ubah': False, 'miskin': False, 'menang': False, 'bantu': False, 'baik': False, 'bahas': False, 'jujur': False, 'ikut': False, 'takut': False, 'sesuai': False, 'lupa': False, 'bayar': 

In [20]:
# menyusun data training dan testing 
trainsize = round(len(featuresets)*0.7) 
random.shuffle(featuresets) 

training_set = featuresets[:trainsize] 
testing_set = featuresets[trainsize:]

In [38]:
classifier = nltk.NaiveBayesClassifier.train(training_set) 
print("Classifier accuracy percent:",(nltk.classify.accuracy(classifier, testing_set))*100) 
classifier.show_most_informative_features(25)

Classifier accuracy percent: 60.0
Most Informative Features
                 ngomong = True           negati : positi =      3.0 : 1.0
                   putih = True           positi : negati =      2.7 : 1.0
                   metro = True           positi : negati =      2.3 : 1.0
                    baik = True           negati : positi =      2.3 : 1.0
                   mampu = True           positi : negati =      2.3 : 1.0
                  bilang = True           negati : positi =      2.3 : 1.0
                   lihat = True           negati : positi =      2.3 : 1.0
                   hitam = True           positi : negati =      1.9 : 1.0
                    jadi = True           negati : positi =      1.9 : 1.0
                  muncul = True           negati : positi =      1.7 : 1.0
                    sama = True           positi : negati =      1.7 : 1.0
                  tayang = True           positi : negati =      1.7 : 1.0
                   pilih = True         

In [39]:
from nltk.metrics.scores import (precision, recall) 
import collections 

refsets = collections.defaultdict(set) 
testsets = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set): 
    refsets[label].add(i) 
    observed = classifier.classify(feats) 
    testsets[observed].add(i) 
    
print('Recall:', recall(refsets['positive'], testsets['positive'])) 
print('Precision:', precision(refsets['positive'], testsets['positive']))

Recall: 0.8833333333333333
Precision: 0.5638297872340425


In [31]:
classifier

In [32]:
#menyimpan model yang telah ditrainning ke file sav 

filename = 'nb_model.sav' 
pickle.dump(classifier, open(filename, 'wb'))

In [33]:
#load model classifier nb dari file 
loaded_model = pickle.load(open(filename, 'rb'))

In [34]:
loaded_model

In [36]:
#melakukan klasifikasi menggunakan model classifier nb yang telah diload 
lsPrediksi = [] 
for (rev, category) in document[trainsize:]: 
    result=loaded_model.classify(find_features(rev)) 
    lsPrediksi.append([rev, result]) 

In [37]:
print(lsPrediksi[:10])

[['Orang Belanda aja peduli sama orang2 indonesia yg berada d daerah terisolir, gimana dg pemerintah indonesia? Zhonk kickandyMetroTV', 'negative'], ['Merinding deh nonton #KickAndyMetroTV', 'positive'], ['Indonesia2. Bahkan kita dididik untuk menjadi rusak.. #kickandymetrotv', 'positive'], ['Parahnya kualitas pendidikan di Indonesia  #kickandymetrotv', 'positive'], ['demi apapun ya kick andy sekarang botak?  #kickandymetrotv', 'positive'], ['jadi merasa malu krn kalah dari org yg tdk sempurna tapi mempunyai yg lebih dari org sempurna #kickandymetrotv', 'negative'], ['Hukum di Indonesia masih jauh dari kata ADIL #KickAndyMetroTV', 'positive'], ['aku kira makin tua makin keladi, malah jd macan ompong. Melempem. kecewa liat amin rais di @kickandymetrotv', 'negative'], ['#kickAndyMetroTV MEDIA harus mengisi lebih banyak ttg kisah sukses di TV, bukan gosip, berita rusuh & acara2 GG JELAS, tai kucing!! #CATET', 'negative'], ['#kickAndyMetroTV jika ingin dihargai orang, hargailah orang lain 

## tunning dataset dan parameter

In [45]:
# menyusun data training dan testing 
trainsize = round(len(featuresets)*0.90) 
random.shuffle(featuresets) 

training_set1 = featuresets[:trainsize] 
testing_set1 = featuresets[trainsize:]

classifier = nltk.NaiveBayesClassifier.train(training_set1) 
print("Classifier accuracy percent:",(nltk.classify.accuracy(classifier, testing_set1))*100) 

refsets1 = collections.defaultdict(set) 
testsets1 = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set1): 
    refsets1[label].add(i) 
    observed = classifier.classify(feats) 
    testsets1[observed].add(i) 
    
print('Recall:', recall(refsets1['positive'], testsets1['positive'])) 
print('Precision:', precision(refsets1['positive'], testsets1['positive']))


Classifier accuracy percent: 67.5
Recall: 0.9166666666666666
Precision: 0.6666666666666666


# B. Support Vector Machine

## B1. Pendekatan Feature Extraction - LSVC

In [26]:
training_set

[({'hitam': False,
   'putih': False,
   'nonton': False,
   'seru': False,
   'hidup': False,
   'tp': False,
   'terima': False,
   'bikin': False,
   'rusak': False,
   'kalah': False,
   'lihat': False,
   'tunggu': False,
   'ngomong': False,
   'bilang': False,
   'coba': False,
   'selamat': False,
   'mati': False,
   'pimpin': False,
   'pilih': False,
   'bicara': False,
   'jaga': True,
   'hitamputih': False,
   'masuk': False,
   'bagus': False,
   'tayang': False,
   'hebat': False,
   'dengar': False,
   'salah': False,
   'langsung': False,
   'mantap': False,
   'bangga': False,
   'dukung': False,
   'pikir': False,
   'tua': False,
   'metrotv': False,
   'lawan': False,
   'buka': False,
   'ni': False,
   'pribadi': False,
   'beda': False,
   'kaya': False,
   'mimpi': False,
   'muncul': False,
   'butuh': False,
   'tindak': False,
   'cerdas': False,
   'lucu': False,
   'besar': False,
   'pulang': False,
   'bawa': False,
   'ubah': False,
   'miskin': False,

In [27]:
testing_set

[({'hitam': False,
   'putih': False,
   'nonton': False,
   'seru': False,
   'hidup': False,
   'tp': False,
   'terima': False,
   'bikin': False,
   'rusak': False,
   'kalah': False,
   'lihat': False,
   'tunggu': False,
   'ngomong': False,
   'bilang': False,
   'coba': False,
   'selamat': False,
   'mati': False,
   'pimpin': False,
   'pilih': False,
   'bicara': False,
   'jaga': False,
   'hitamputih': False,
   'masuk': False,
   'bagus': False,
   'tayang': False,
   'hebat': False,
   'dengar': False,
   'salah': False,
   'langsung': False,
   'mantap': False,
   'bangga': False,
   'dukung': False,
   'pikir': False,
   'tua': False,
   'metrotv': False,
   'lawan': False,
   'buka': False,
   'ni': False,
   'pribadi': False,
   'beda': False,
   'kaya': False,
   'mimpi': False,
   'muncul': False,
   'butuh': False,
   'tindak': False,
   'cerdas': False,
   'lucu': False,
   'besar': False,
   'pulang': False,
   'bawa': False,
   'ubah': False,
   'miskin': False

In [46]:
svm_model =nltk.classify.SklearnClassifier(LinearSVC())
svm_model

<SklearnClassifier(LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0))>

In [47]:
svm_model.train(training_set)

<SklearnClassifier(LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0))>

In [48]:
accuracy = nltk.classify.accuracy(svm_model,testing_set)

from nltk.metrics.scores import (precision, recall) 
import collections 

refsets_svm = collections.defaultdict(set) 
testsets_svm = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set): 
    refsets_svm[label].add(i) 
    observed = svm_model.classify(feats) 
    testsets_svm[observed].add(i) 

print('Accuracy: ', accuracy)
print('Recall:', recall(refsets_svm['positive'], testsets_svm['positive'])) 
print('Precision:', precision(refsets_svm['positive'], testsets_svm['positive']))

Accuracy:  0.5833333333333334
Recall: 0.8666666666666667
Precision: 0.5531914893617021


In [35]:
#menyimpan model yang telah ditrainning ke file sav
filename = 'svm_model_fitur.sav'
pickle.dump(svm_model, open(filename, 'wb'))

In [37]:
#load model classifier nb dari file 
loaded_model = pickle.load(open(filename, 'rb'))
loaded_model

<SklearnClassifier(LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
          intercept_scaling=1, loss='squared_hinge', max_iter=1000,
          multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
          verbose=0))>

## Tuning SVM => SVC

In [49]:
svm_model_svc =nltk.classify.SklearnClassifier(SVC())
svm_model_svc.train(training_set)

accuracy = nltk.classify.accuracy(svm_model_svc,testing_set)

from nltk.metrics.scores import (precision, recall) 
import collections 

refsets_svm1 = collections.defaultdict(set) 
testsets_svm1 = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set): 
    refsets_svm1[label].add(i) 
    observed = svm_model_svc.classify(feats) 
    testsets_svm1[observed].add(i) 

print('Accuracy: ', accuracy)
print('Recall:', recall(refsets_svm1['positive'], testsets_svm1['positive'])) 
print('Precision:', precision(refsets_svm1['positive'], testsets_svm1['positive']))

Accuracy:  0.6083333333333333
Recall: 0.5833333333333334
Precision: 0.6140350877192983


In [78]:
svm_model_svc =nltk.classify.SklearnClassifier(SVC(C=10, max_iter=100, tol=0.000001, kernel='sigmoid'))
svm_model_svc.train(training_set)

accuracy = nltk.classify.accuracy(svm_model_svc,testing_set)

from nltk.metrics.scores import (precision, recall) 
import collections 

refsets_svm1 = collections.defaultdict(set) 
testsets_svm1 = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set): 
    refsets_svm1[label].add(i) 
    observed = svm_model_svc.classify(feats) 
    testsets_svm1[observed].add(i) 

print('Accuracy: ', accuracy)
print('Recall:', recall(refsets_svm1['positive'], testsets_svm1['positive'])) 
print('Precision:', precision(refsets_svm1['positive'], testsets_svm1['positive']))

Accuracy:  0.5416666666666666
Recall: 0.8666666666666667
Precision: 0.5252525252525253


In [59]:
svm_model_svc

<SklearnClassifier(SVC(C=1.0, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='scale', kernel='rbf',
    max_iter=-1, probability=False, random_state=None, shrinking=True,
    tol=0.001, verbose=False))>

## tuning linear SVC

In [58]:
svm_model_tun =nltk.classify.SklearnClassifier(LinearSVC(C=10, tol=0.00000005, max_iter=10000))
svm_model_tun.train(training_set)

accuracy = nltk.classify.accuracy(svm_model_tun,testing_set)

from nltk.metrics.scores import (precision, recall) 
import collections 

refsets_svm = collections.defaultdict(set) 
testsets_svm = collections.defaultdict(set) 

for i, (feats, label) in enumerate(testing_set): 
    refsets_svm[label].add(i) 
    observed = svm_model_tun.classify(feats) 
    testsets_svm[observed].add(i) 

print('Accuracy: ', accuracy)
print('Recall:', recall(refsets_svm['positive'], testsets_svm['positive'])) 
print('Precision:', precision(refsets_svm['positive'], testsets_svm['positive']))

Accuracy:  0.5916666666666667
Recall: 0.9
Precision: 0.5567010309278351


## B2. Pipeline dan GridSearch

In [41]:
df['Text Tweet']

0      Undang @N_ShaniJKT48 ke hitamputih, pemenang S...
1      Selamat berbuka puasa Semoga amal ibadah hari ...
2      Ada nih di trans7 hitam putih, dia dpt penghar...
3            selamat ya mas @adietaufan masuk hitamputih
4                      Asiknya nonton Hitam Putih Trans7
                             ...                        
395    ini apa banget deh gw paling kesel klo orang2 ...
396    Orang miskin semakin miskin klo sekolah melaku...
397    ga boLeh emosi, cepat tua, nonton #matanajwame...
398    dr penampilan saja kyk preman taunya bkin kisr...
399    Jawab aja ga usah berbelit-belit. Muter2 ga je...
Name: Text Tweet, Length: 400, dtype: object

In [79]:
list_data = []
for i in df['Text Tweet']:
    list_data.append(i)
list_data

['Undang @N_ShaniJKT48 ke hitamputih, pemenang SSK JKT48 harusnya mJKT48 ini lebih Layak di Undang karena prestasinya',
 'Selamat berbuka puasa Semoga amal ibadah hari ni diterima Allah #hitamputih',
 'Ada nih di trans7 hitam putih, dia dpt penghargaan juga di norwegia #hitamputih',
 'selamat ya mas @adietaufan masuk hitamputih',
 'Asiknya nonton Hitam Putih Trans7',
 '@TRANS7 acara paling komplit dan menarik apalagi ada hitam putih',
 'hitam putih T7 inspiratif banget',
 'Suka banget dengan acara hitam putih',
 'Keren lu bro #HitamPutihTrans7',
 'Tadi ada yg liat hitam putih di trans7 ga, Ada sanggu ganteng',
 'cinta mengikat silaturahmi di hati ... #LunaMaya #hitamputihtrans7 .... https://www.instagram.com/p/BTqszJ3jO9A/',
 'Terima kasih pak.... Sudah mau membantu kami untuk menyekolahkan adik saya.... #hitamputihtrans7',
 'Semoga lancar hitamputihtrans7',
 'Trans7 Hitam Putih terbaik https://www.instagram.com/p/BTYyTXMgVKd/',
 'Acara hitam putih paling bagus buat di lihat',
 '@TRANS

In [92]:
df['sentiment_label'] = df['Sentiment'].apply(lambda x: 0 if x=='negative' else 1)
Y = df['sentiment_label']

In [80]:
import re
pat1 = r'@[A-Za-z0-9_]+' #menghapus @mention
pat2 = r'https?://[A-Za-z0-9./]+' #menghapus url
pat3 = r'#[A-Za-z0-9]+' #menghapus hashtag
pat4 = r'\[A-Za-z0-9]+'#menghapus angka dalam kata
pat5 = r'\<[A-Za-z0-9+_>]+' #menghapus format maps yang error
pat6 = r'[0-9]+' #menghapus karakter angka dalam satu rangkaian lebih dari satu
pattern = re.compile('\W')  #menghapus spasi berlebih

combined_pat = r'|'.join((pat1, pat2, pat3,pat4, pat5, pat6)) #pembuatan kombinasi filter

list_data_bersih1 = []

for kata in list_data:
    dataBersih1 = re.sub(combined_pat,'',str(kata)) #proses filtering
    list_data_bersih1.append(dataBersih1) #data bersih disimpan
    
list_data_bersih = []
for k in list_data_bersih1:   
    dataBersih2 = re.sub(pattern,' ',str(k)) #menghapus karakter non alphanumeric
    dataBersih3 = re.sub(r'\b\w{1,1}\b', '', dataBersih2) #mengapus karakter 1 digit
    list_data_bersih.append(dataBersih3) #menyimpan dalam list

In [91]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split, StratifiedKFold, cross_val_score
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.model_selection import GridSearchCV

vectorizer = TfidfVectorizer(stop_words = stop, #deklarasi stopwords
                             use_idf=True, #menginisiasi penggunaan inverse document
                             ngram_range=(1,3), #deklarasi interval n-gram
                             norm='l2', #menginisiasi penggunaan normalisasi
                             smooth_idf=False, #menginiasi penggunaan inverse document frequency
                             min_df=2 #menginisiasi minimal jumlah kata dalam tweet
                            )

# melakukan pemisahan data training dan testing
X_train, X_test, y_train, y_test = train_test_split(list_data_bersih, Y, test_size=0.30)

In [101]:
import numpy as np
#pendefinisian kfold
kfolds = StratifiedKFold(n_splits=5, shuffle=True, random_state=1)

np.random.seed(1)

svm_grid = make_pipeline(vectorizer, 
                            SVC(probability=True, kernel="linear", class_weight="balanced"))

grid_svm = GridSearchCV(svm_grid,
                    param_grid = {'svc__C': [0.01, 0.1, 2], 
                                  'svc__kernel' : ['poly', 'rbf'],
                                 'svc__gamma' : [1, 0.1, 0.001, 0.0001],
                                 'svc__max_iter' : [100, 1000, 500]}, 
                    cv = kfolds,
                    scoring="roc_auc",
                    verbose=1,   
                    n_jobs=-1)

grid_svm.fit(X_train, y_train)
grid_svm.score(X_test, y_test)

Fitting 5 folds for each of 72 candidates, totalling 360 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  76 tasks      | elapsed:    3.0s
[Parallel(n_jobs=-1)]: Done 360 out of 360 | elapsed:   11.0s finished
C:\Users\HP\anaconda3\lib\site-packages\sklearn\feature_extraction\text.py:382: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['baiknya', 'batas', 'benarnya', 'bener', 'berulang', 'dalamnya', 'dibagi', 'galanya', 'gamblangnya', 'gini', 'gininya', 'harinya', 'kesini', 'kurangnya', 'mata', 'menerus', 'mereta', 'merta', 'musabab', 'musababnya', 'napa', 'nyata', 'olah', 'ratanya', 'reka', 'rupa', 'sebenar', 'sedalam', 'segamblang', 'segini', 'segmen', 'sejelas', 'sekurang', 'sempet', 'tama', 'yakinnya'] not in stop_words.
  warnings.warn('Your stop_words may be inconsistent with '


0.8574825174825176

In [102]:
grid_svm.best_score_

0.8321839080459771

In [103]:
from sklearn.metrics import make_scorer, accuracy_score, f1_score
from sklearn.metrics import roc_curve, auc
from sklearn.metrics import confusion_matrix, roc_auc_score, recall_score, precision_score

def hasil_evaluasi(model, X, y):
    pred_proba = model.predict_proba(X)[:, 1]
    pred = model.predict(X)        

    acc = accuracy_score(y, pred)
    f1 = f1_score(y, pred)
    prec = precision_score(y, pred)
    rec = recall_score(y, pred)
    result = {'auc': auc, 'f1': f1, 'acc': acc, 'precision': prec, 'recall': rec}
    return result

hasil_evaluasi(grid_svm.best_estimator_, X_test, y_test)

{'auc': <function sklearn.metrics._ranking.auc(x, y)>,
 'f1': 0.7307692307692308,
 'acc': 0.7666666666666667,
 'precision': 0.7755102040816326,
 'recall': 0.6909090909090909}

# C. Logistic Regression

In [24]:
X = df['Text Tweet']
Y = df['Sentiment']

In [25]:
X

0      Undang @N_ShaniJKT48 ke hitamputih, pemenang S...
1      Selamat berbuka puasa Semoga amal ibadah hari ...
2      Ada nih di trans7 hitam putih, dia dpt penghar...
3            selamat ya mas @adietaufan masuk hitamputih
4                      Asiknya nonton Hitam Putih Trans7
                             ...                        
395    ini apa banget deh gw paling kesel klo orang2 ...
396    Orang miskin semakin miskin klo sekolah melaku...
397    ga boLeh emosi, cepat tua, nonton #matanajwame...
398    dr penampilan saja kyk preman taunya bkin kisr...
399    Jawab aja ga usah berbelit-belit. Muter2 ga je...
Name: Text Tweet, Length: 400, dtype: object

In [26]:
Y

0      positive
1      positive
2      positive
3      positive
4      positive
         ...   
395    negative
396    negative
397    negative
398    negative
399    negative
Name: Sentiment, Length: 400, dtype: object

In [27]:
list_kalimat = []
for i in X:
    list_kalimat.append(i)
list_kalimat

['Undang @N_ShaniJKT48 ke hitamputih, pemenang SSK JKT48 harusnya mJKT48 ini lebih Layak di Undang karena prestasinya',
 'Selamat berbuka puasa Semoga amal ibadah hari ni diterima Allah #hitamputih',
 'Ada nih di trans7 hitam putih, dia dpt penghargaan juga di norwegia #hitamputih',
 'selamat ya mas @adietaufan masuk hitamputih',
 'Asiknya nonton Hitam Putih Trans7',
 '@TRANS7 acara paling komplit dan menarik apalagi ada hitam putih',
 'hitam putih T7 inspiratif banget',
 'Suka banget dengan acara hitam putih',
 'Keren lu bro #HitamPutihTrans7',
 'Tadi ada yg liat hitam putih di trans7 ga, Ada sanggu ganteng',
 'cinta mengikat silaturahmi di hati ... #LunaMaya #hitamputihtrans7 .... https://www.instagram.com/p/BTqszJ3jO9A/',
 'Terima kasih pak.... Sudah mau membantu kami untuk menyekolahkan adik saya.... #hitamputihtrans7',
 'Semoga lancar hitamputihtrans7',
 'Trans7 Hitam Putih terbaik https://www.instagram.com/p/BTYyTXMgVKd/',
 'Acara hitam putih paling bagus buat di lihat',
 '@TRANS

In [28]:
import re
pat1 = r'@[A-Za-z0-9_]+' #menghapus @mention
pat2 = r'https?://[A-Za-z0-9./]+' #menghapus url
pat3 = r'#[A-Za-z0-9]+' #menghapus hashtag
pat4 = r'\[A-Za-z0-9]+'#menghapus angka dalam kata
pat5 = r'\<[A-Za-z0-9+_>]+' #menghapus format maps yang error
pat6 = r'[0-9]+' #menghapus karakter angka dalam satu rangkaian lebih dari satu
pattern = re.compile('\W')  #menghapus spasi berlebih

combined_pat = r'|'.join((pat1, pat2, pat3,pat4, pat5, pat6)) #pembuatan kombinasi filter

list_data_bersih1 = []

for kata in list_kalimat:
    dataBersih1 = re.sub(combined_pat,'',str(kata)) #proses filtering
    list_data_bersih1.append(dataBersih1) #data bersih disimpan
    
list_data_bersih = []
for k in list_data_bersih1:   
    dataBersih2 = re.sub(pattern,' ',str(k)) #menghapus karakter non alphanumeric
    dataBersih3 = re.sub(r'\b\w{1,1}\b', '', dataBersih2) #mengapus karakter 1 digit
    list_data_bersih.append(dataBersih3) #menyimpan dalam list


In [29]:
list_data_bersih

['Undang  ke hitamputih  pemenang SSK JKT harusnya mJKT ini lebih Layak di Undang karena prestasinya',
 'Selamat berbuka puasa Semoga amal ibadah hari ni diterima Allah ',
 'Ada nih di trans hitam putih  dia dpt penghargaan juga di norwegia ',
 'selamat ya mas  masuk hitamputih',
 'Asiknya nonton Hitam Putih Trans',
 ' acara paling komplit dan menarik apalagi ada hitam putih',
 'hitam putih  inspiratif banget',
 'Suka banget dengan acara hitam putih',
 'Keren lu bro ',
 'Tadi ada yg liat hitam putih di trans ga  Ada sanggu ganteng',
 'cinta mengikat silaturahmi di hati            ',
 'Terima kasih pak     Sudah mau membantu kami untuk menyekolahkan adik saya     ',
 'Semoga lancar hitamputihtrans',
 'Trans Hitam Putih terbaik ',
 'Acara hitam putih paling bagus buat di lihat',
 ' undang  di acara hitam putih ya dia jebolan dangdut academi pinter nyanyi lagu india suaranya keren',
 'Bagus Rancangan Seperti ini di TRANS HitamPutih  Sambil Dakwah Hiburannya  Terima kasih Ustadz Wijayanto 

In [30]:
nltk.download('punkt') 
from nlp_id.stopword import StopWord 
stopword = StopWord()

punctuation = list(string.punctuation)
stop = stopword.get_stopword() + punctuation + ['rt', 'via', '…','•','“']

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\HP\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [31]:
stop

['ada',
 'adalagi',
 'adalah',
 'adanya',
 'adapun',
 'agak',
 'agak-agak',
 'agaknya',
 'agar',
 'aja',
 'akan',
 'akankah',
 'akankan',
 'akhir',
 'akhir-akhirnya',
 'akhirannya',
 'akhiri',
 'akhirinya',
 'akhirnya',
 'aku',
 'akulah',
 'akunya',
 'akurat',
 'akutu',
 'ala',
 'alamak',
 'alhamdulillah',
 'alhasil',
 'amat',
 'amat-amat',
 'amatlah',
 'anda',
 'anda-anda',
 'andai',
 'andalah',
 'antar',
 'antara',
 'antaranya',
 'apa',
 'apa-apanya',
 'apaan',
 'apabila',
 'apaitu',
 'apakah',
 'apalagi',
 'apanya',
 'apasaja',
 'apatah',
 'apesnya',
 'arah',
 'artinya',
 'asal',
 'asalkan',
 'asumsinya',
 'asumsikan',
 'atas',
 'atas-atas',
 'atas-batas',
 'ataspun',
 'atau',
 'ataukah',
 'ataupun',
 'awal',
 'awalnya',
 'bagai',
 'bagaikan',
 'bagaimana',
 'bagaimanakah',
 'bagaimanapun',
 'bagi',
 'bagi-bagi',
 'bagian',
 'bagikan',
 'bahasakan',
 'bahasanya',
 'bahkan',
 'bahwa',
 'bahwasanya',
 'baik',
 'bak',
 'bakal',
 'bakal-bakal',
 'bakalan',
 'balik',
 'balikan',
 'balikk

In [32]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(stop_words = stop, #deklarasi stopwords
                             use_idf=True, #menginisiasi penggunaan inverse document
                             ngram_range=(1,3), #deklarasi interval n-gram
                             norm='l2', #menginisiasi penggunaan normalisasi
                             smooth_idf=False, #menginiasi penggunaan inverse document frequency
                             min_df=2 #menginisiasi minimal jumlah kata dalam tweet
                            )


In [34]:
# melakukan pemisahan data training dan testing
X_train, X_test, y_train, y_test = train_test_split(list_data_bersih, Y, test_size=0.40)

In [35]:
from sklearn.pipeline import Pipeline
LogisticRegression = Pipeline([('vect', vectorizer),
                     ('clf', LogisticRegression(random_state=0))])

model_logit = LogisticRegression.fit(X_train, y_train)
model_logit

C:\Users\HP\anaconda3\lib\site-packages\sklearn\feature_extraction\text.py:382: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['baiknya', 'batas', 'benarnya', 'bener', 'berulang', 'dalamnya', 'dibagi', 'galanya', 'gamblangnya', 'gini', 'gininya', 'harinya', 'kesini', 'kurangnya', 'mata', 'menerus', 'mereta', 'merta', 'musabab', 'musababnya', 'napa', 'nyata', 'olah', 'ratanya', 'reka', 'rupa', 'sebenar', 'sedalam', 'segamblang', 'segini', 'segmen', 'sejelas', 'sekurang', 'sempet', 'tama', 'yakinnya'] not in stop_words.
  warnings.warn('Your stop_words may be inconsistent with '


Pipeline(memory=None,
         steps=[('vect',
                 TfidfVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.float64'>,
                                 encoding='utf-8', input='content',
                                 lowercase=True, max_df=1.0, max_features=None,
                                 min_df=2, ngram_range=(1, 3), norm='l2',
                                 preprocessor=None, smooth_idf=False,
                                 stop_words=['ada', 'adalagi', 'adalah',
                                             'adanya', 'adapun', 'agak',
                                             'agak-a...
                                 strip_accents=None, sublinear_tf=False,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=None, use_idf=True,
                                 vocabulary=None)),
                ('c

In [37]:
import numpy as np
from sklearn.metrics import confusion_matrix, classification_report

y_test2=np.array(y_test)

print(classification_report(y_test2, model_logit.predict(X_test))) 
print(confusion_matrix(y_test2, model_logit.predict(X_test)))

              precision    recall  f1-score   support

    negative       0.67      0.87      0.76        78
    positive       0.83      0.60      0.70        82

    accuracy                           0.73       160
   macro avg       0.75      0.73      0.73       160
weighted avg       0.75      0.73      0.73       160

[[68 10]
 [33 49]]


# EDA

In [104]:
df

Id Sentiment           Acara TV  Jumlah Retweet  \
0      1  positive  HitamPutihTransTV              12   
1      2  positive  HitamPutihTransTV               6   
2      3  positive  HitamPutihTransTV               9   
3      4  positive  HitamPutihTransTV               2   
4      5  positive  HitamPutihTransTV               1   
..   ...       ...                ...             ...   
395  396  negative   MataNajwaMetroTV               0   
396  397  negative   MataNajwaMetroTV               0   
397  398  negative   MataNajwaMetroTV               0   
398  399  negative   MataNajwaMetroTV               0   
399  400  negative   MataNajwaMetroTV               0   

                                            Text Tweet  sentiment_label  
0    Undang @N_ShaniJKT48 ke hitamputih, pemenang S...                1  
1    Selamat berbuka puasa Semoga amal ibadah hari ...                1  
2    Ada nih di trans7 hitam putih, dia dpt penghar...                1  
3          selamat ya mas @adietaufan masuk hitamputih                1  
4                    Asiknya nonton Hitam Putih Trans7                1  
..                                                 ...              ...  
395  ini apa banget deh gw paling kesel klo orang2 ...                0  
396  Orang miskin semakin miskin klo sekolah melaku...                0  
397  ga boLeh emosi, cepat tua, nonton #matanajwame...                0  
398  dr penampilan saja kyk preman taunya bkin kisr...                0  
399  Jawab aja ga usah berbelit-belit. Muter2 ga je...                0  

[400 rows x 6 columns]

In [106]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 400 entries, 0 to 399
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Id               400 non-null    int64 
 1   Sentiment        400 non-null    object
 2   Acara TV         400 non-null    object
 3   Jumlah Retweet   400 non-null    int64 
 4   Text Tweet       400 non-null    object
 5   sentiment_label  400 non-null    int64 
dtypes: int64(3), object(3)
memory usage: 18.9+ KB


In [114]:
from collections import Counter
Counter(df['Sentiment'])

Counter({'positive': 200, 'negative': 200})